In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Fri Aug 22 12:27:12 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   70C    P8             11W /   70W |       0MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [ ]:
from psutil import virtual_memory
ram_gb = virtual_memory().total / 1e9
print('Your runtime has {:.1f} gigabytes of available RAM (CPU)\n'.format(ram_gb))

if ram_gb < 20:
  print('Not using a high-RAM runtime')
else:
  print('You are using a high-RAM runtime!')

Your runtime has 54.8 gigabytes of available RAM

You are using a high-RAM runtime!


In [ ]:
import psutil
import torch
import pandas as pd

# --- RAM CPU ---
ram = psutil.virtual_memory()
ram_total = ram.total / 1e9
ram_used = (ram.total - ram.available) / 1e9
ram_free = ram.available / 1e9

# --- GPU VRAM ---
if torch.cuda.is_available():
    gpu_name = torch.cuda.get_device_name(0)
    props = torch.cuda.get_device_properties(0)
    vram_total = props.total_memory / 1e9
    vram_allocated = torch.cuda.memory_allocated(0) / 1e9
    vram_reserved = torch.cuda.memory_reserved(0) / 1e9
    vram_free = vram_total - vram_reserved
else:
    gpu_name = "Aucun GPU"
    vram_total = vram_allocated = vram_reserved = vram_free = 0

# --- Tableau résumé ---
data = {
    "Type": ["CPU RAM", "GPU VRAM"],
    "Total (Go)": [f"{ram_total:.2f}", f"{vram_total:.2f}"],
    "Utilisée (Go)": [f"{ram_used:.2f}", f"{vram_allocated:.2f}"],
    "Libre (Go)": [f"{ram_free:.2f}", f"{vram_free:.2f}"],
}

df = pd.DataFrame(data)
print(f"GPU détecté : {gpu_name}\n")
print(df.to_string(index=False))

GPU détecté : Tesla T4

    Type Total (Go) Utilisée (Go) Libre (Go)
 CPU RAM      13.61          3.09      10.52
GPU VRAM      15.83          0.00      15.83


In [ ]:
!git+https://github.com/huggingface/transformers
!pip install torch
!pip install accelerate
!pip install librosa
!pip install elevenlabs
!pip install speechmatics-batch
!pip install assemblyai

/bin/bash: line 1: git+https://github.com/huggingface/transformers: No such file or directory
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.7/823.7 kB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.1/50.1 kB 2.0 MB/s eta 0:00:00


# Imports

In [ ]:
from transformers import AutoModelForSpeechSeq2Seq, AutoProcessor
import torch
import soundfile as sf
import librosa
from io import BytesIO
from elevenlabs.client import ElevenLabs
import os
import shutil
import math
#import spaces
from speechmatics.batch import AsyncClient, JobConfig, JobType, TranscriptionConfig
import assemblyai
from google.colab import userdata

from datasets import load_dataset, Audio
import asyncio

import aiohttp
import random
from concurrent.futures import ThreadPoolExecutor
from tqdm.asyncio import tqdm
from tqdm.asyncio import tqdm_asyncio
import pandas as pd

import time
import logging

from google.colab import drive

# Initializations

In [ ]:
### Initializations

device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"*** Device: {device}")

# Configurations
el_client = ElevenLabs(api_key=userdata.get('elevenlabs_api_key'))

assemblyai.settings.api_key = userdata.get('assemblyai_api_key')
ass_config = assemblyai.TranscriptionConfig(language_code="pl",
                                            speech_model=assemblyai.SpeechModel.best)

model_id = "openai/whisper-large-v3-turbo"
hf_model = AutoModelForSpeechSeq2Seq.from_pretrained(
    model_id, low_cpu_mem_usage=True, use_safetensors=True
).to(device)
hf_processor = AutoProcessor.from_pretrained(model_id)

spm_client = AsyncClient(api_key=userdata.get('speechmatics_api_key'))
spm_config = JobConfig(
    type=JobType.TRANSCRIPTION,
    transcription_config=TranscriptionConfig(language="pl", diarization=None))

# Mount Google Drive
drive.mount('/content/drive')

# Define the path to the directory in the Drive
directory_path = "/content/drive/MyDrive/DS/IA Gen/Transcription/results"

logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)

# Supprimer tous les handlers existants (dont le StreamHandler par défaut)
logger.handlers = []

# Ajouter uniquement le FileHandler
fh = logging.FileHandler("transcription_spm_logs.txt")
fh.setLevel(logging.INFO)
formatter = logging.Formatter("%(asctime)s [%(levelname)s] %(message)s")
fh.setFormatter(formatter)
logger.addHandler(fh)

*** Device: cpu


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/1.62G [00:00<?, ?B/s]

generation_config.json: 0.00B [00:00, ?B/s]

preprocessor_config.json:   0%|          | 0.00/340 [00:00<?, ?B/s]

...

merges.txt: 0.00B [00:00, ?B/s]

normalizer.json: 0.00B [00:00, ?B/s]

added_tokens.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

ValueError: mount failed

In [ ]:
# Mount Google Drive
drive.mount('/content/drive')

# Define the path to the directory in the Drive
directory_path = "/content/drive/MyDrive/DS/IA Gen/Transcription/results"

logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)

# Supprimer tous les handlers existants (dont le StreamHandler par défaut)
logger.handlers = []

# Ajouter uniquement le FileHandler
fh = logging.FileHandler("transcription_spm_logs.txt")
fh.setLevel(logging.INFO)
formatter = logging.Formatter("%(asctime)s [%(levelname)s] %(message)s")
fh.setFormatter(formatter)
logger.addHandler(fh)

Mounted at /content/drive


# Load data

In [ ]:
# Define the path to the directory in the Drive
save_path = "/content/drive/MyDrive/DS/IA Gen/Transcription/data/common_voice_pl_test"

## From Hugging Face datasets

In [ ]:
!pip install huggingface_hub==0.30.2
!pip install datasets==3.2.0

In [ ]:
from datasets import load_dataset
from google.colab import userdata

cv_pl_test = load_dataset(
    "mozilla-foundation/common_voice_17_0",
    "pl",
    split="test",
  token=userdata.get('HF_TOKEN'),
  trust_remote_code=True # added
)

print(cv_pl_test)
print(f"Nombre d’exemples : {len(cv_pl_test)}")
print("Un échantillon :", cv_pl_test[0])

audio/pl/validated/pl_validated_0.tar:   0%|          | 0.00/1.46G [00:00<?, ?B/s]

audio/pl/validated/pl_validated_1.tar:   0%|          | 0.00/1.34G [00:00<?, ?B/s]

audio/pl/validated/pl_validated_2.tar:   0%|          | 0.00/1.37G [00:00<?, ?B/s]

audio/pl/validated/pl_validated_3.tar:   0%|          | 0.00/404M [00:00<?, ?B/s]

train.tsv:   0%|          | 0.00/6.69M [00:00<?, ?B/s]

...

Generating invalidated split: 0 examples [00:00, ? examples/s]


Reading metadata...: 0it [00:00, ?it/s]
Reading metadata...: 6605it [00:00, 47489.58it/s]


Generating validated split: 0 examples [00:00, ? examples/s]


Reading metadata...: 0it [00:00, ?it/s]
Reading metadata...: 5536it [00:00, 55349.23it/s]
Reading metadata...: 11145it [00:00, 55780.44it/s]
Reading metadata...: 16724it [00:00, 52731.98it/s]
Reading metadata...: 22016it [00:00, 51859.29it/s]
Reading metadata...: 27497it [00:00, 52884.40it/s]
Reading metadata...: 33046it [00:00, 53746.48it/s]
Reading metadata...: 38430it [00:00, 53337.09it/s]
Reading metadata...: 43770it [00:00, 52436.04it/s]
Reading metadata...: 49020it [00:00, 52348.01it/s]
Reading metadata...: 54259it [00:01, 52187.13it/s]
Reading metadata...: 60115it [00:01, 54105.64it/s]
Reading metadata...: 65531it [00:01, 53524.61it/s]
Reading metadata...: 71037it [00:01, 53976.59it/s]
Reading metadata...: 76439it [00:01, 52300.85it/s]
Reading metadata...: 81682it [00:01, 51751.86it/s]
Reading metadata...: 86866it [00:01, 50411.93it/s]
Reading metadata...: 95529it [00:01, 60881.82it/s]
Reading metadata...: 105190it [00:01, 71318.93it/s]
Reading metadata...: 114927it [00:01, 789

Dataset({
    features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment', 'variant'],
    num_rows: 9230
})
Nombre d’exemples : 9230
Un échantillon : {'client_id': '02eb087ff2dda32b8dd01a85b4693569a62d56033bf17d7f0565aa45fa29b850e53f808baf94fef3d89be8a5ed0432675594297e47f8e5ea0ddfe86e81a21711', 'path': '/root/.cache/huggingface/datasets/downloads/extracted/9cbc8c1f7b3532cb9e4f180b6121aac14995e1ea1484a4d40099f7dd3a92eb43/pl_test_0/common_voice_pl_24005493.mp3', 'audio': {'path': '/root/.cache/huggingface/datasets/downloads/extracted/9cbc8c1f7b3532cb9e4f180b6121aac14995e1ea1484a4d40099f7dd3a92eb43/pl_test_0/common_voice_pl_24005493.mp3', 'array': array([0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
       7.43369128e-06, 1.14012100e-05, 8.05014497e-06]), 'sampling_rate': 48000}, 'sentence': '"Ostatnie słowa wymówił syczącym szeptem i ze złośliwym uśmiechem."', 'up_votes': 2, 'down_votes': 0, 'age': '', 'gender': ''

In [ ]:
cv_pl_test.save_to_disk(save_path)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


Saving the dataset (0/1 shards):   0%|          | 0/9230 [00:00<?, ? examples/s]

## From drive

In [ ]:
from datasets import load_from_disk

cv_pl_test = load_from_disk(save_path)
cv_pl_test = cv_pl_test.cast_column("audio", Audio(decode=False))
print(cv_pl_test)

Dataset({
    features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment', 'variant'],
    num_rows: 9230
})


In [ ]:
import pandas as pd

# Convert the dataset to a pandas DataFrame
cv_pl_df = cv_pl_test.to_pandas()

# Display the first 5 rows of the DataFrame
display(cv_pl_df.head())

client_id  \
0  02eb087ff2dda32b8dd01a85b4693569a62d56033bf17d...   
1  039674fdf440f2c9e53ff991cf27230071a2d969342dfd...   
2  04bb285ec98789c6485651e8e7c5c5897de0462ce196bc...   
3  068bf7cf01fb28afca5df71713cdbf9f52eb54e3d9eba2...   
4  09e8fc1e934239cfd3124d1ca7f1c4f3d27cde45951bb4...   

                                                path  \
0  /root/.cache/huggingface/datasets/downloads/ex...   
1  /root/.cache/huggingface/datasets/downloads/ex...   
2  /root/.cache/huggingface/datasets/downloads/ex...   
3  /root/.cache/huggingface/datasets/downloads/ex...   
4  /root/.cache/huggingface/datasets/downloads/ex...   

                                               audio  \
0  {'bytes': b'ID3\x04\x00\x00\x00\x00\x00#TSSE\x...   
1  {'bytes': b'ID3\x04\x00\x00\x00\x00\x00#TSSE\x...   
2  {'bytes': b'ID3\x04\x00\x00\x00\x00\x00#TSSE\x...   
3  {'bytes': b'ID3\x04\x00\x00\x00\x00\x00#TSSE\x...   
4  {'bytes': b'ID3\x04\x00\x00\x00\x00\x00#TSSE\x...   

                                            sentence  up_votes  down_votes  \
0  "Ostatnie słowa wymówił syczącym szeptem i ze ...         2           0   
1                       Gdzież tu powód do wyrzutów?         5           0   
2                                          Lubię go.         4           1   
3                                — To mi nie pomaga.         3           1   
4  Wciąż ludzie wysiadają przed zamkiem, z miasta...        24           1   

        age          gender accent locale segment variant  
0                                      pl                  
1                                      pl                  
2  thirties  male_masculine            pl                  
3                                      pl                  
4                                      pl

In [ ]:
display(cv_pl_df.tail())

client_id  \
9225  cc1cb6742a93f7bd4425c46348ab3da82a83869d3ad13e...   
9226  cc1cb6742a93f7bd4425c46348ab3da82a83869d3ad13e...   
9227  cc1cb6742a93f7bd4425c46348ab3da82a83869d3ad13e...   
9228  cc1cb6742a93f7bd4425c46348ab3da82a83869d3ad13e...   
9229  cc1cb6742a93f7bd4425c46348ab3da82a83869d3ad13e...   

                                                   path  \
9225  /root/.cache/huggingface/datasets/downloads/ex...   
9226  /root/.cache/huggingface/datasets/downloads/ex...   
9227  /root/.cache/huggingface/datasets/downloads/ex...   
9228  /root/.cache/huggingface/datasets/downloads/ex...   
9229  /root/.cache/huggingface/datasets/downloads/ex...   

                                                  audio  \
9225  {'bytes': b'ID3\x04\x00\x00\x00\x00\x01"TXXX\x...   
9226  {'bytes': b'ID3\x04\x00\x00\x00\x00\x01"TXXX\x...   
9227  {'bytes': b'ID3\x04\x00\x00\x00\x00\x01"TXXX\x...   
9228  {'bytes': b'ID3\x04\x00\x00\x00\x00\x01"TXXX\x...   
9229  {'bytes': b'ID3\x04\x00\x00\x00\x00\x01"TXXX\x...   

                                             sentence  up_votes  down_votes  \
9225            "Wydzielał się z niej zapach pleśni."         2           1   
9226                       "Długo żadnej odpowiedzi."         2           0   
9227  — Zostanę zjedzony przez twojego papę i ty też.         2           0   
9228    "Widok tego lisa wprawił mnie we wściekłość."         2           0   
9229   "Nagle usłyszałem tuż obok przeraźliwy krzyk."         2           0   

     age gender accent locale segment variant  
9225                       pl                  
9226                       pl                  
9227                       pl                  
9228                       pl                  
9229                       pl

In [ ]:
cv_pl_df['sentence'].iloc[100:105]

100                   Pan Bóg łaskaw — sypiam jak suseł.
101          W tym miejscu całuje mnie już ósmy chłopak.
102    To był szybki, ale na pewno przemyślany i rozs...
103        Był to w prostej linii dziad Seweryna Baryki.
104                                   — Ot, co wymyślił.
Name: sentence, dtype: object

# Functions

## Hugging Face, ElevenLabs, & AssemblyAI

In [ ]:
# ---- PARTIES BLOQUANTES EN THREAD ----
def run_librosa_and_hf(hf_audio_filepath):
    """Lecture audio + transcription HuggingFace"""
    try:
        audio, sr = librosa.load(hf_audio_filepath, sr=16000)
        input_features = hf_processor(audio, sampling_rate=16000, return_tensors="pt")
        input_features = input_features.input_features.to(device)
        attention_mask = torch.ones_like(input_features).to(device)

        predicted_ids = hf_model.generate(input_features, language="pl", attention_mask=attention_mask)
        transcription = hf_processor.batch_decode(predicted_ids, skip_special_tokens=True)[0]
    except Exception as e:
        transcription = f"Error transcription: {e}"

    return transcription
###

def run_assemblyai(ass_audio_filepath):
    """Transcription AssemblyAI"""
    try:
        transcriber = assemblyai.Transcriber()
        transcript = transcriber.transcribe(ass_audio_filepath, ass_config)
        if transcript.status == assemblyai.TranscriptStatus.error:
            transcription = f"Transcription failed: {transcript.error}"
        else:
            transcription = transcript.text
    except Exception as e:
        transcription = f"Erreur transcription : {e}"

    return transcription
###

def run_elevenlabs(el_audio_filepath):
    """Transcription ElevenLabs"""
    try:
        audio, sr = librosa.load(el_audio_filepath, sr=16000)
        tmp_buffer = BytesIO()
        sf.write(tmp_buffer, audio, sr, format="WAV")
        tmp_buffer.seek(0)

        resp = el_client.speech_to_text.convert(
            file=tmp_buffer,
            model_id="scribe_v1",
            language_code="pol",
            diarize=False,
            timestamps_granularity="word",
            tag_audio_events=False
        )
        transcription = resp.text # Access text using .text attribute
    except Exception as e:
        transcription = f"Erreur transcription : {e}"

    return transcription
###

# ---- FONCTION ASYNC PRINCIPALE ----
async def transcribe_audio_async(audio_filepath, executor):
    loop = asyncio.get_event_loop()
    """
    spm_semaphore = asyncio.Semaphore(1)

    async def run_spm(spm_audio_filepath, retries=5, base_delay=1):
        start_time = time.perf_counter()
        for attempt in range(retries):
            try:
                async with spm_semaphore:
                    logger.info(f"[SPM] Submit job: {spm_audio_filepath} (attempt {attempt+1})")

                    job = await spm_client.submit_job(spm_audio_filepath, config=spm_config)
                    result = await spm_client.wait_for_completion(job.id)

                status = getattr(result, "status", None) or result.get("status")
                if status == "failed":
                    error_msg = getattr(result, "error", None) or result.get("error", "inconnue")
                    if attempt + 1 < retries:
                        delay = base_delay * (2 ** attempt) + random.uniform(0, 0.5)
                        logger.warning(f"[SPM] Job failed (retry {attempt+1}) in {delay:.1f}s")
                        await asyncio.sleep(delay)
                        continue
                    else:
                        elapsed = time.perf_counter() - start_time
                        return f"Erreur transcription (SPM): {error_msg}", elapsed

                transcription = result.transcript_text.removeprefix("SPEAKER UU: ")

                elapsed = time.perf_counter() - start_time
                logger.info(f"[SPM] Done transcription: {spm_audio_filepath} (took {elapsed:.2f}s)")
                return transcription, elapsed

            except Exception as e:
                elapsed = time.perf_counter() - start_time
                logger.error(f"[SPM] Exception transcription {spm_audio_filepath}: {e}")
                return f"Erreur transcription : {e}", elapsed
    """

    def run_with_timer(func, fp, label):
        start_time = time.perf_counter()
        transcription = func(fp)
        elapsed = time.perf_counter() - start_time
        logger.info(f"[{label}] Done transcription: {fp} (took {elapsed:.2f}s)")
        return transcription, elapsed

    hf_future = loop.run_in_executor(executor, run_with_timer, run_librosa_and_hf, audio_filepath, "HF")
 #   spm_future = asyncio.create_task(run_spm(audio_filepath))
    ass_future = loop.run_in_executor(executor, run_with_timer, run_assemblyai, audio_filepath, "AssemblyAI")
    el_future = loop.run_in_executor(executor, run_with_timer, run_elevenlabs, audio_filepath, "ElevenLabs")

    hf_transcription, hf_time = await hf_future
#    spm_transcription, spm_time = await spm_future
    ass_transcription, ass_time = await ass_future
    el_transcription, el_time = await el_future

    return {
        "file_path": audio_filepath,
        "hf_transcription": hf_transcription,
        "hf_time": hf_time,
#        "spm_transcription": spm_transcription,
 #       "spm_time": spm_time,
        "ass_transcription": ass_transcription,
        "ass_time": ass_time,
        "el_transcription": el_transcription,
        "el_time": el_time
    }

In [ ]:
async def process_all_with_progress(list_file_paths, max_workers=5):
    start_time_total = time.perf_counter()
    results = [None] * len(list_file_paths)  # Pré-allocation

    with ThreadPoolExecutor(max_workers=max_workers) as executor:

        async def indexed_task(idx, fp):
            start_time_file = time.perf_counter()
            res = await transcribe_audio_async(fp, executor)
            elapsed_file = time.perf_counter() - start_time_file
            logger.info(f"[TOTAL] Finished {fp} in {elapsed_file:.2f}s")
            return idx, res

        tasks = [indexed_task(i, fp) for i, fp in enumerate(list_file_paths)]

        for fut in tqdm(asyncio.as_completed(tasks), total=len(tasks), desc="Transcriptions"):
            idx, res = await fut
            results[idx] = res

    elapsed_total = time.perf_counter() - start_time_total
    logger.info(f"[TOTAL] All files processed: {len(list_file_paths)} files in {elapsed_total:.2f}s")
    logger.info(f"[TOTAL] Average per file: {elapsed_total / len(list_file_paths):.2f}s")

    return results

## Speechmatics

In [ ]:
# ---- FONCTION DE TRANSCRIPTION UNITÉ ----
async def run_spm(spm_audio_filepath):
    spm_transcription = ""
    try:
        # ⚡️ appels async au client Speechmatics
        job = await spm_client.submit_job(spm_audio_filepath, config=spm_config)
        result = await spm_client.wait_for_completion(job.id)

        transcription = result.transcript_text.removeprefix("SPEAKER UU: ")
        spm_transcription = transcription

    except Exception as e:
        spm_transcription = f"Erreur transcription : {e}"

    return spm_transcription


# ---- FONCTION WRAPPER AVEC LOGS ----
async def transcribe_audio(audio_filepath, semaphore=None):
    async def run_with_timer(fp):
        start_time = time.perf_counter()
        transcription = await run_spm(fp)
        elapsed = time.perf_counter() - start_time
        logger.info(f"[SPM] Done transcription: {fp} (took {elapsed:.2f}s)")
        return transcription, elapsed

    if semaphore:
        async with semaphore:
            spm_transcription, spm_time = await run_with_timer(audio_filepath)
    else:
        spm_transcription, spm_time = await run_with_timer(audio_filepath)

    return {
        "file_path": audio_filepath,
        "spm_transcription": spm_transcription,
        "spm_time": spm_time
    }


# ---- FONCTION POUR UN BATCH ----
async def process_spm(list_file_paths, max_concurrent=5):
    start_time_total = time.perf_counter()
    results = [None] * len(list_file_paths)  # pré-allocation
    semaphore = asyncio.Semaphore(max_concurrent)

    async def indexed_task(idx, fp):
        res = await transcribe_audio(fp, semaphore=semaphore)
        return idx, res

    # ✅ on crée des tasks (et pas de simples coroutines)
    tasks = [asyncio.create_task(indexed_task(i, fp)) for i, fp in enumerate(list_file_paths)]

    # Exécution parallèle + barre de progression
    async for fut in tqdm(asyncio.as_completed(tasks), total=len(tasks), desc="Transcriptions"):
        idx, res = await fut
        results[idx] = res

    elapsed_total = time.perf_counter() - start_time_total
    logger.info(f"[TOTAL] All files processed: {len(list_file_paths)} files in {elapsed_total:.2f}s")
    logger.info(f"[TOTAL] Average per file: {elapsed_total / len(list_file_paths):.2f}s")

    return results

# Main process

In [ ]:
num_rows = len(cv_pl_test)
batch_size = 100
num_batches = math.ceil(num_rows / batch_size)

start_batch = 0

## HugginFace, ElevenLabs, AssemblyAI

In [ ]:
for i in range(start_batch, num_batches):
    start_idx = i * batch_size
    end_idx = min(((i + 1) * batch_size)-1, num_rows)

    # Get the audio datas and save them locally
    mp3_folder = f"mp3_batch_{i}"
    # Create the directory if it doesn't exist
    os.makedirs(mp3_folder, exist_ok=True)
    list_path = []
    list_sentence = []

    # Process the batch from dataset
    for ex in cv_pl_test.select(range(start_idx, end_idx)):
        audio_path = ex['audio']['path']
        sentence = ex['sentence']
        save_path = os.path.join(mp3_folder, os.path.basename(audio_path))
        with open(save_path, "wb") as f:
            f.write(ex['audio']['bytes'])
        list_path.append(save_path)
        list_sentence.append(sentence)

    print(mp3_folder, " loaded")

    df = pd.DataFrame({
        'file_path': list_path,
        'sentence': list_sentence
    })

    # Process the transcriptions
    results = await process_all_with_progress(list_path, max_workers=5)
    df_results = pd.DataFrame(results)
    df_results["total_time"] = df_results[["hf_time", "ass_time", "el_time"]].sum(axis=1)

    # Merge results with batch dataframe
    df_batch = df.merge(df_results, on='file_path', how='left')

    # Sauvegarder en CSV avec numéro de lot
    csv_filename = os.path.join(directory_path, f"batch_{i+1}.csv")
    df_batch.to_csv(csv_filename, sep=";", index=False)

    shutil.copy("transcription_logs.txt", directory_path)

    print(f"Line {start_idx} to {end_idx} saved in {csv_filename}")

    # Remove mp3 folder
    if os.path.exists(mp3_folder):
        shutil.rmtree(mp3_folder)

mp3_batch_1  loaded


Transcriptions:   0%|          | 0/99 [00:00<?, ?it/s]INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_1/common_voice_pl_20638465.mp3 (took 0.85s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_1/common_voice_pl_39562969.mp3 (took 0.62s)
INFO:__main__:[HF] Done transcription: mp3_batch_1/common_voice_pl_23913589.mp3 (took 0.68s)
INFO:__main__:[HF] Done transcription: mp3_batch_1/common_voice_pl_39562969.mp3 (took 2.17s)
INFO:__main__:[HF] Done transcription: mp3_batch_1/common_voice_pl_20638465.mp3 (took 2.26s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_1/common_voice_pl_23913589.mp3 (took 0.52s)
INFO:__main__:[HF] Done transcription: mp3_batch_1/common_voice_pl_37353781.mp3 (took 0.82s)
INFO:__main__:[AssemblyAI] Done transcription: mp3_batch_1/common_voice_pl_39562969.mp3 (took 3.69s)
INFO:__main__:[TOTAL] Finished mp3_batch_1/common_voice_pl_39562969.mp3 in 3.69s
Transcriptions:   1%|          | 1/99 [00:03<06:02,  3.70s/it]INFO:__main__:[AssemblyAI] 

Line 100 to 199 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_2.csv
mp3_batch_2  loaded


Transcriptions:   0%|          | 0/99 [00:00<?, ?it/s]INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_2/common_voice_pl_22446266.mp3 (took 0.40s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_2/common_voice_pl_20606453.mp3 (took 0.45s)
INFO:__main__:[HF] Done transcription: mp3_batch_2/common_voice_pl_22446266.mp3 (took 2.08s)
INFO:__main__:[HF] Done transcription: mp3_batch_2/common_voice_pl_20606453.mp3 (took 2.08s)
INFO:__main__:[HF] Done transcription: mp3_batch_2/common_voice_pl_22723318.mp3 (took 1.24s)
INFO:__main__:[HF] Done transcription: mp3_batch_2/common_voice_pl_20613487.mp3 (took 0.69s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_2/common_voice_pl_22723318.mp3 (took 0.86s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_2/common_voice_pl_20613487.mp3 (took 0.45s)
INFO:__main__:[AssemblyAI] Done transcription: mp3_batch_2/common_voice_pl_22446266.mp3 (took 3.46s)
INFO:__main__:[TOTAL] Finished mp3_batch_2/common_voice_pl_22446266.m

Line 200 to 299 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_3.csv
mp3_batch_3  loaded


...

Line 9000 to 9099 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_91.csv
mp3_batch_91  loaded


Transcriptions:   0%|          | 0/99 [00:00<?, ?it/s]INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_91/common_voice_pl_25894565.mp3 (took 0.11s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_91/common_voice_pl_22707851.mp3 (took 0.12s)
INFO:__main__:[HF] Done transcription: mp3_batch_91/common_voice_pl_22707851.mp3 (took 2.26s)
INFO:__main__:[HF] Done transcription: mp3_batch_91/common_voice_pl_25894565.mp3 (took 2.30s)
INFO:__main__:[HF] Done transcription: mp3_batch_91/common_voice_pl_25321410.mp3 (took 2.13s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_91/common_voice_pl_25321410.mp3 (took 0.11s)
INFO:__main__:[HF] Done transcription: mp3_batch_91/common_voice_pl_25894568.mp3 (took 0.76s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_91/common_voice_pl_25894568.mp3 (took 0.11s)
INFO:__main__:[AssemblyAI] Done transcription: mp3_batch_91/common_voice_pl_22707851.mp3 (took 3.50s)
INFO:__main__:[TOTAL] Finished mp3_batch_91/common_voice_pl_

Line 9100 to 9199 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_92.csv
mp3_batch_92  loaded


Transcriptions:   0%|          | 0/30 [00:00<?, ?it/s]INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_92/common_voice_pl_20656522.mp3 (took 0.13s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_92/common_voice_pl_25233706.mp3 (took 0.10s)
INFO:__main__:[HF] Done transcription: mp3_batch_92/common_voice_pl_20618581.mp3 (took 2.05s)
INFO:__main__:[HF] Done transcription: mp3_batch_92/common_voice_pl_25233706.mp3 (took 2.30s)
INFO:__main__:[HF] Done transcription: mp3_batch_92/common_voice_pl_20656522.mp3 (took 2.40s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_92/common_voice_pl_20618581.mp3 (took 0.09s)
INFO:__main__:[HF] Done transcription: mp3_batch_92/common_voice_pl_20631193.mp3 (took 0.82s)
INFO:__main__:[ElevenLabs] Done transcription: mp3_batch_92/common_voice_pl_20631193.mp3 (took 0.10s)
INFO:__main__:[AssemblyAI] Done transcription: mp3_batch_92/common_voice_pl_25233706.mp3 (took 3.45s)
INFO:__main__:[TOTAL] Finished mp3_batch_92/common_voice_pl_

Line 9200 to 9230 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_93.csv


## SpeechMatics

In [ ]:
for i in range(start_batch, num_batches):
    start_idx = i * batch_size
    end_idx = min(((i + 1) * batch_size)-1, num_rows)

    # Get the audio datas and save them locally
    mp3_folder = f"mp3_batch_{i}"
    # Create the directory if it doesn't exist
    os.makedirs(mp3_folder, exist_ok=True)
    list_path = []
    list_sentence = []

    # Process the batch from dataset
    for ex in cv_pl_test.select(range(start_idx, end_idx)):
        audio_path = ex['audio']['path']
        sentence = ex['sentence']
        save_path = os.path.join(mp3_folder, os.path.basename(audio_path))
        with open(save_path, "wb") as f:
            f.write(ex['audio']['bytes'])
        list_path.append(save_path)
        list_sentence.append(sentence)

    print(mp3_folder, " loaded")

    df = pd.DataFrame({
        'file_path': list_path,
        'sentence': list_sentence
    })

    # Process the transcriptions
    results = await process_spm(list_path, 10)


    df_results = pd.DataFrame(results)

    # Merge results with batch dataframe
    df_batch = df.merge(df_results, on='file_path', how='left')

    # Sauvegarder en CSV avec numéro de lot
    csv_filename = os.path.join(directory_path, f"batch_spm_{i+1}.csv")
    df_batch.to_csv(csv_filename, sep=";", index=False)

    shutil.copy("transcription_spm_logs.txt", directory_path)

    print(f"Line {start_idx} to {end_idx} saved in {csv_filename}")

    # Remove mp3 folder
    if os.path.exists(mp3_folder):
        shutil.rmtree(mp3_folder)

mp3_batch_0  loaded


Transcriptions:   2%|▏         | 2/99 [00:10<08:27,  5.23s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_20633386.mp3 (took 10.47s)
INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_28085422.mp3 (took 10.48s)
INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_24005493.mp3 (took 10.56s)
Transcriptions:   5%|▌         | 5/99 [00:10<02:38,  1.69s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_20605240.mp3 (took 10.57s)
INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_20603604.mp3 (took 10.88s)
INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_20603513.mp3 (took 10.88s)
Transcriptions:   8%|▊         | 8/99 [00:10<01:22,  1.10it/s]INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_20603955.mp3 (took 10.92s)
INFO:__main__:[SPM] Done transcription: mp3_batch_0/common_voice_pl_20605185.mp3 (took 15.51s)
Transcriptions:  12%|█▏        | 12/99 [00:20<02:46,  

Line 0 to 99 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_spm_1.csv
mp3_batch_1  loaded


Transcriptions:   3%|▎         | 3/99 [00:10<04:55,  3.08s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20605241.mp3 (took 10.51s)
INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20605231.mp3 (took 10.56s)
INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20604568.mp3 (took 10.57s)
INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20606445.mp3 (took 11.35s)
Transcriptions:   8%|▊         | 8/99 [00:15<02:33,  1.69s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20603694.mp3 (took 15.53s)
INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20630185.mp3 (took 15.94s)
Transcriptions:  11%|█         | 11/99 [00:20<02:47,  1.90s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20603638.mp3 (took 10.25s)
INFO:__main__:[SPM] Done transcription: mp3_batch_1/common_voice_pl_20604370.mp3 (took 10.74s)
Transcriptions:  15%|█▌        | 15/99 [00:25<02:07, 

Line 100 to 199 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_spm_2.csv
mp3_batch_2  loaded


...

Line 9000 to 9099 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_spm_91.csv
mp3_batch_91  loaded


Transcriptions:   2%|▏         | 2/99 [00:10<08:21,  5.17s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_25894520.mp3 (took 10.42s)
INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_27656729.mp3 (took 10.42s)
INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_27656732.mp3 (took 10.80s)
Transcriptions:  12%|█▏        | 12/99 [00:20<01:50,  1.27s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_25894533.mp3 (took 10.40s)
INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_25894536.mp3 (took 10.46s)
Transcriptions:  15%|█▌        | 15/99 [00:25<02:24,  1.72s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_25894535.mp3 (took 15.43s)
INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_25894592.mp3 (took 10.25s)
Transcriptions:  20%|██        | 20/99 [00:30<01:44,  1.32s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_91/common_voice_pl_39878393

Line 9100 to 9199 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_spm_92.csv
mp3_batch_92  loaded


Transcriptions:   7%|▋         | 2/30 [00:10<02:25,  5.20s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20618581.mp3 (took 10.45s)
INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20603919.mp3 (took 10.48s)
INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20839686.mp3 (took 10.80s)
Transcriptions:  17%|█▋        | 5/30 [00:10<00:43,  1.75s/it]INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20604308.mp3 (took 10.86s)
INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20631193.mp3 (took 10.89s)
INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20839687.mp3 (took 11.30s)
Transcriptions:  27%|██▋       | 8/30 [00:11<00:21,  1.03it/s]INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20631038.mp3 (took 11.33s)
INFO:__main__:[SPM] Done transcription: mp3_batch_92/common_voice_pl_20839685.mp3 (took 16.91s)
Transcriptions:  57%|█████▋    | 17/30 [00:26<

Line 9200 to 9230 saved in /content/drive/MyDrive/DS/IA Gen/Transcription/results/batch_spm_93.csv


# Utils

In [ ]:
from IPython.display import Audio

# Écouter dans le notebook
Audio("common_voice_pl_20774047.mp3")

In [ ]:
cv_pl_test.features

{'client_id': Value('string'),
 'path': Value('string'),
 'audio': Audio(sampling_rate=None, decode=False, stream_index=None),
 'sentence': Value('string'),
 'up_votes': Value('int64'),
 'down_votes': Value('int64'),
 'age': Value('string'),
 'gender': Value('string'),
 'accent': Value('string'),
 'locale': Value('string'),
 'segment': Value('string'),
 'variant': Value('string'),
 'continuation': Value('string')}

# Work

## ElevenLabs

In [ ]:
%pip install gradio transformers elevenlabs

### Import libraries

#### Subtask:
Import the necessary libraries for building the Gradio app and performing transcriptions.


In [ ]:
import gradio as gr
from transformers import AutoModelForSpeechSeq2Seq, AutoProcessor
import torch
import soundfile as sf
import librosa
from io import BytesIO
from elevenlabs.client import ElevenLabs

### Define transcription functions

In [ ]:
def transcribe_audio_el(audio_filepath):
    """
    Transcribes an audio file using ElevenLabs's scribe_v1 and Hugging Face's
    whisper-large-v3-turbo models in Polish, in parallel.

    Args:
        audio_filepath (str): The path to the audio file.

    Returns:
        tuple: A tuple containing the transcriptions from scribe_v1 and
               whisper-large-v3-turbo, respectively.
    """
    audio, sr = librosa.load(audio_filepath, sr=16000)
    tmp_buffer = BytesIO()
    sf.write(tmp_buffer, audio, sr, format="WAV")
    tmp_buffer.seek(0)

    elevenlabs_transcription = ""



    try:
        resp = client.speech_to_text.convert(
            file=tmp_buffer,
            model_id="scribe_v1",
            language_code="pol",
            diarize=False,
            timestamps_granularity="word",
            tag_audio_events=False
        )
        elevenlabs_transcription = resp.text # Access text using .text attribute
    except Exception as e:
        elevenlabs_transcription = f"Erreur transcription : {e}"


    return elevenlabs_transcription

def transcribe_audio_hf(audio_filepath):
    """
    Transcribes an audio file using ElevenLabs's scribe_v1 and Hugging Face's
    whisper-large-v3-turbo models in Polish, in parallel.

    Args:
        audio_filepath (str): The path to the audio file.

    Returns:
        tuple: A tuple containing the transcriptions from scribe_v1 and
               whisper-large-v3-turbo, respectively.
    """
    audio, sr = librosa.load(audio_filepath, sr=16000)
    hf_transcription = ""

    try:
        input_features = hf_processor(
            audio,
            sampling_rate=16000,
            return_tensors="pt"
        )
        input_features = input_features.input_features.to(device)
        attention_mask = torch.ones_like(input_features).to(device)

        predicted_ids = hf_model.generate(input_features, language="pl", attention_mask=attention_mask)
        hf_transcription = hf_processor.batch_decode(
            predicted_ids, skip_special_tokens=True
        )[0]
    except Exception as e:
        hf_transcription = f"Error with Hugging Face transcription: {e}"


    return hf_transcription


def clear_audio():
    return None, None, None

In [ ]:
def get_elevenlabs_credit():
    """
    Retrieves ElevenLabs credit information.
    Args:
        None
    Returns:
        int : credits left
    """
    print("* get_elevenlabs_credit")
    credit_left = 0
    try:
        user_info = client.user.subscription.get()

        if user_info: # Check if subscription info exists
            credit_left = user_info.character_limit - user_info.character_count
        else:
            print("ElevenLabs subscription information not available.")
    except Exception as e:
        print(f"Error retrieving ElevenLabs credit information: {e}")
    finally:
        return credit_left

def calc_credits(init_credit):
    """
    Calculates the number of ElevenLabs credits used.
    Args:
        init_credit (int): initial credit

    Returns:
        int : credits used by the last transaction
        int : credits left
    """
    print("* calc_credits : init_credit=",init_credit)
    delta = 0
    new_credit_left = 0

    try:
        user_info = client.user.subscription.get()
        if user_info: # Check if subscription info exists
            print("user_info.character_limit=", user_info.character_limit)
            print("user_info.character_count=", user_info.character_count)
            new_credit_left = user_info.character_limit - (user_info.character_count+5)
            delta = init_credit - new_credit_left
            print("delta=",delta)
    except Exception as e:
        print(f"Error retrieving ElevenLabs credit information: {e}")
    finally:
        return delta, new_credit_left

In [ ]:
from google.colab import userdata


client = ElevenLabs(api_key=userdata.get('elevenlabs_api_key'))

device = "cuda:0" if torch.cuda.is_available() else "cpu"
model_id = "openai/whisper-large-v3-turbo"
hf_model = AutoModelForSpeechSeq2Seq.from_pretrained(
    model_id, low_cpu_mem_usage=True, use_safetensors=True
).to(device)
hf_processor = AutoProcessor.from_pretrained(model_id)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:104: UserWarning: 
Error while fetching `HF_TOKEN` secret value from your vault: 'Requesting secret HF_TOKEN timed out. Secrets can only be fetched when running from the Colab UI.'.
You are not authenticated with the Hugging Face Hub in this notebook.
If the error persists, please let us know by opening an issue on GitHub (https://github.com/huggingface/huggingface_hub/issues/new).
  warnings.warn(


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/1.62G [00:00<?, ?B/s]

generation_config.json: 0.00B [00:00, ?B/s]

preprocessor_config.json:   0%|          | 0.00/340 [00:00<?, ?B/s]

...

tokenizer.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

normalizer.json: 0.00B [00:00, ?B/s]

added_tokens.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

In [ ]:
# Init ElevenLabs credits
init_credit = get_elevenlabs_credit()

with gr.Blocks() as interface:
    gr.Markdown("# 🇵🇱  Polish Audio Transcription")

    with gr.Row():
        audio_input = gr.Audio(sources=["microphone"], type="filepath",
                               label="Record your audio in Polish")
        with gr.Column():
            submit_transcript = gr.Button("Extract transcription", variant="primary")
            clear_button = gr.Button("Clear")

    with gr.Row():
        with gr.Column():
            el_output = gr.Textbox(label="Scribe v1 Transcription")
            with gr.Row():
                el_credits = gr.Number(label="Available credits", value=init_credit, interactive=False)
                el_used = gr.Number(label="Credits used by transcription", interactive=False)
        with gr.Column():
            hf_output = gr.Textbox(label="Whisper Large v3 Turbo Transcription")

### Processing

    submit_transcript.click(transcribe_audio_hf, inputs=audio_input,
                            outputs=hf_output)
    submit_transcript.click(transcribe_audio_el, inputs=audio_input,
                            outputs=el_output) \
                     .then(calc_credits, inputs=[el_credits],
                           outputs=[el_used, el_credits])
    clear_button.click(fn=clear_audio, inputs=[],
                       outputs=[audio_input, hf_output, el_output, el_used])

* get_elevenlabs_credit


In [ ]:
interface.launch(share=True, debug=True)

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://643ef288c87b9a7c28.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


* calc_credits : init_credit= 9990
user_info.character_limit= 10000
user_info.character_count= 10
delta= 5
Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://a60464bd6efd8c42d3.gradio.live
Killing tunnel 127.0.0.1:7861 <> https://fe99c3395ccfa5673b.gradio.live
Killing tunnel 127.0.0.1:7862 <> https://51e7e895c3f1d6c9e2.gradio.live
Killing tunnel 127.0.0.1:7863 <> https://643ef288c87b9a7c28.gradio.live


## SpeechMatics

In [ ]:
!pip install gradio speechmatics-batch

In [ ]:
import gradio as gr
import asyncio
from speechmatics.batch import AsyncClient, JobConfig, JobType, TranscriptionConfig
from google.colab import userdata

In [ ]:
spm_client = AsyncClient(api_key=userdata.get('speechmatics_api_key'))

# Configure transcription
spm_config = JobConfig(
    type=JobType.TRANSCRIPTION,
    transcription_config=TranscriptionConfig(language="pl", diarization=None))

In [ ]:
async def transcribe_audio_spm(audio):
    # Submit job
    job = await spm_client.submit_job(audio, config=spm_config)
    print(f"Job submitted: {job.id}")

    # Wait for completion
    result = await spm_client.wait_for_completion(
        job.id,
#        polling_interval=2.0,
#        timeout=300.0
    )

    # Access results
    print(result)
    print(f"Transcript: {result.transcript_text}")
    print(f"Confidence: {result.confidence}")

    return result.transcript_text.removeprefix("SPEAKER UU: ")

def clear_audio():
    return None, None

ModuleNotFoundError: No module named 'speechmatics.batch_client'

In [ ]:
#### Gradio interface
with gr.Blocks() as demo:
    gr.Markdown("# 🇵🇱  Polish Audio Transcription")
    audio_input = gr.Audio(sources=["microphone"], type="filepath",
                           label="Record your audio in Polish")
    submit_transcript = gr.Button("Extract transcription", variant="primary")
    spm_output = gr.Textbox(label="Speechmatics Transcription")

    clear_button = gr.Button("Clear")

### Processing

    submit_transcript.click(transcribe_audio_spm, inputs=audio_input,
                            outputs=spm_output)
    clear_button.click(fn=clear_audio, inputs=[], outputs=[audio_input, spm_output])

In [ ]:
demo.queue().launch(share=True, debug=True)

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://7b38aa42d92b889f80.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Job submitted: g08s5oqksq
Transcript(format='2.9', job=JobInfo(id='g08s5oqksq', created_at='2025-08-01T08:52:46.998Z', data_name='audio.wav', duration=1, text_name=None, tracking=None), metadata=RecognitionMetadata(created_at='2025-08-01T08:52:57.604331Z', type='transcription', transcription_config={'language': 'pl', 'operating_point': 'enhanced'}, orchestrator_version='2025.07.28781+f8b0678540.HEAD', translation_errors=None, summarization_errors=None, sentiment_analysis_errors=None, topic_detection_errors=None, auto_chapters_errors=None, alignment_config=None, output_config=None, language_pack_info={'adapted': False, 'itn': False, 'language_description': 'Polish', 'word_delimiter': ' ', 'writing_direction': 'left-to-right'}, language_identification=None), results=[], translations=None, summary=None, sentiment_analysis=None, topics=None, chapters=None, audio_events=None, audio_event_summary=None)
Transcript: 
Confidence: None
Job submitted: c6mmo8hmye
Transcript(format='2.9', job=JobIn

## AssemblyAI

In [ ]:
!pip install -U assemblyai gradio

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.5/59.5 MB 15.7 MB/s eta 0:00:00
  Attempting uninstall: gradio
    Found existing installation: gradio 5.38.2
    Uninstalling gradio-5.38.2:
      Successfully uninstalled gradio-5.38.2


In [ ]:
import assemblyai
import gradio as gr
import asyncio

from google.colab import userdata

# Set your API key here, which can be found on your Dashboard as mentioned above.
assemblyai.settings.api_key = userdata.get('assemblyai_api_key')
config = assemblyai.TranscriptionConfig(language_code="pl",
                                        speech_model=assemblyai.SpeechModel.best)

def transcribe_audio_ass(audio_path):
    transcriber = assemblyai.Transcriber()
    transcript = transcriber.transcribe(audio_path, config)
    if transcript.status == assemblyai.TranscriptStatus.error:
        print(f"Transcription failed: {transcript.error}")

    return transcript.text

def clear_audio():
    return None, None

In [ ]:
t = transcribe_audio_ass("/tmp/gradio/6de5562c859b0cac89010f62d09b14b74baf0bcfc9c8266bcda249fca6fbba11/audio.wav")
print(t)

Dzień dobry.


In [ ]:
#### Gradio interface
with gr.Blocks() as demo:
    gr.Markdown("# 🇵🇱  Polish Audio Transcription")
    audio_input = gr.Audio(sources=["microphone"], type="filepath",
                           label="Record your audio in Polish")
    submit_transcript = gr.Button("Extract transcription", variant="primary")
    ass_output = gr.Textbox(label="AssemblyAI Transcription")

    clear_button = gr.Button("Clear")

### Processing

    submit_transcript.click(transcribe_audio_ass, inputs=audio_input,
                            outputs=ass_output)
    clear_button.click(fn=clear_audio, inputs=[], outputs=[audio_input, ass_output])

In [ ]:
demo.queue().launch(share=True, debug=True)

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://ce74ba3ab781738a94.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


audio:  /tmp/gradio/6de5562c859b0cac89010f62d09b14b74baf0bcfc9c8266bcda249fca6fbba11/audio.wav


Traceback (most recent call last):
  File "/usr/local/lib/python3.11/dist-packages/gradio/queueing.py", line 626, in process_events
    response = await route_utils.call_process_api(
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/gradio/route_utils.py", line 350, in call_process_api
    output = await app.get_blocks().process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/gradio/blocks.py", line 2239, in process_api
    result = await self.call_function(
             ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/gradio/blocks.py", line 1744, in call_function
    prediction = await fn(*processed_input)
                 ^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/local/lib/python3.11/dist-packages/gradio/utils.py", line 884, in async_wrapper
    response = await f(*args, **kwargs)
               ^^^^^^^^^^^^^^^^^^^^^^^^
  File "/tmp/ipython-input-3351614638.p

Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7860 <> https://ce74ba3ab781738a94.gradio.live


In [ ]:
import gradio as gr


def greet(name):
    return "Hello " + name + "!"

css = """
    .gradio-container textarea {
        font-size: 25px !important;
        }
    .gradio-container button {
        font-size: 25px !important;
    }
        #transcript_box span {
            font-size: 25px;
            font-weight: bold;
        }
    .gradio-container label span {
    font-size: 25px !important;
    color: red !important;
}
"""


# Create a Gradio interface with a textbox input, a button to trigger the greet function, and an output textbox.
with gr.Blocks(css=css) as demo:
    name = gr.Textbox(label="Name", elem_id="transcript_box")
    output = gr.Textbox(label="Output Box")
    greet_btn = gr.Button("Greet")
    font_size_slider = gr.Slider(10, 50, value=16, step=1, label="Font Size")

    # Connect the greet function to the button click event.
    greet_btn.click(fn=greet, inputs=name, outputs=output, api_name="greet")

    # Connect the font size slider to the update_font_size function to change the font size of all text elements.
    #ont_size_slider.change(fn=update_font_size, inputs=font_size_slider, outputs=[name, output])

demo.launch(debug=True)

It looks like you are running Gradio on a hosted Jupyter notebook, which requires `share=True`. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://ee0b723eac1e8504be.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7862 <> https://ee0b723eac1e8504be.gradio.live


In [ ]:
import gradio as gr

# 1. Définition de la fonction de mise à jour
# Elle prend une taille de police en entrée et retourne du code HTML
def update_text_style(font_size):

    html_content = f"<p style='font-size: {font_size}px; color: blue;'>Mon titre</p><p style='font-size: {font_size}px;'>Ce texte a une taille de {font_size} pixels. klneqff erfhjeogmdgrhjrg erfdmhdg eqdglqdhgn sgqdgqgv msqsdj qsdgmgjg qsgdfgfg qsgdg</p>"

    return html_content


# 2. Création de l'interface Gradio
with gr.Blocks() as demo:
    gr.Markdown("## Contrôler la taille de la police dynamiquement avec un Slider")

    # Le slider qui servira de contrôleur
    font_slider = gr.Slider(
        minimum=10,
        maximum=60,
        value=20,
        step=1,
        label="Taille de la police (px)"
    )

    # Le composant HTML qui affichera le résultat
    # On lui donne une valeur initiale pour l'affichage au démarrage
    custom_font_size = "24px"
    custom_color = "blue"

    # Utiliser une f-string pour insérer les styles dans le HTML
    styled_text = "<p style='font-size: 25px; color: blue;'>Mon titre</p>"
    gr.Markdown(styled_text)


    styled_text_output = gr.HTML(
        value="<p style='font-size: 20px;'>Ce texte a une taille de 20 pixels.</p>"
    )

    # 3. Connexion du slider à la fonction
    # L'événement 'change' est plus efficace que 'input' car il ne se déclenche
    # que lorsque l'utilisateur relâche le curseur du slider.
    font_slider.change(
        fn=update_text_style,
        inputs=font_slider,
        outputs=styled_text_output
    )

demo.launch()

It looks like you are running Gradio on a hosted Jupyter notebook, which requires `share=True`. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://7b2319e516bed000bf.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
import gradio as gr

# Le script JavaScript pour basculer le thème
js_theme_script = """
() => {
    const url = new URL(window.location);
    if (url.searchParams.get('__theme') !== 'dark') {
        url.searchParams.set('__theme', 'dark');
    } else {
        url.searchParams.set('__theme', 'light');
    }
    window.location.href = url.href;
}
"""

with gr.Blocks() as demo:
    gr.Markdown("# Application Gradio avec changement de thème")

    # Bouton pour basculer le thème
    theme_button = gr.Button("Passer au thème sombre/clair")
    theme_button.click(None, js=js_theme_script)

    # Le reste de votre application Gradio
    name = gr.Textbox(label="Nom")
    output = gr.Textbox(label="Message de sortie")
    greet_btn = gr.Button("Saluer")

    def greet(name):
        return "Bonjour " + name + "!"

    greet_btn.click(fn=greet, inputs=name, outputs=output, api_name="greet")

demo.launch(share=True)

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://697d8a86ed0fa41062.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
import gradio as gr

# La liste des couleurs de base
colors = [
    "slate", "gray", "zinc", "neutral", "stone", "red", "orange",
    "amber", "yellow", "lime", "green", "emerald", "teal", "cyan",
    "sky", "blue", "indigo", "violet", "purple", "fuchsia", "pink", "rose"
]

# Un peu de JavaScript pour gérer le rechargement et la lecture de l'URL
# Ce script fait deux choses :
# 1. La fonction `on_load` lit le paramètre `__theme` de l'URL et renvoie le nom de la couleur.
# 2. Le `select` sur le composant Radio déclenche un rechargement de la page avec le nouveau thème.
js_code = """
// Fonction pour lire le thème depuis l'URL au chargement
function on_load() {
  const url = window.location.href;
  const params = new URL(url).searchParams;
  const theme = params.get('__theme');
  if (theme) {
    return theme;
  }
  return 'slate'; // Couleur par défaut si aucun thème n'est dans l'URL
}

// Fonction pour recharger la page avec un nouveau thème
function on_select(evt) {
  const url = window.location.href;
  const new_theme = evt.target.value;
  const params = new URL(url).searchParams;
  params.set('__theme', new_theme);

  // Construit la nouvelle URL et navigue vers elle
  window.location.href = '?' + params.toString();
}
"""

with gr.Blocks(theme=gr.themes.Soft(), title="Aperçu des Couleurs Gradio") as demo:
    gr.Markdown("# Aperçu Visuel des Couleurs de Base Gradio")
    gr.Markdown("Choisissez une couleur pour recharger l'aperçu avec le thème correspondant.")

    with gr.Row():
        # Sélecteur de couleur
        color_selector = gr.Radio(
            colors,
            label="🎨 Choisissez une couleur de thème",
            value="slate", # Valeur par défaut
            elem_id="color_selector"
        )

        # Le conteneur pour l'aperçu des composants
        with gr.Group():
            gr.Markdown("### Aperçu des Composants")
            gr.Textbox(label="Champ de texte", value="Exemple de texte")
            gr.Dropdown(label="Menu déroulant", choices=["Option 1", "Option 2"], value="Option 1")
            gr.Slider(label="Curseur", value=65, minimum=0, maximum=100)
            with gr.Row():
                gr.Button("Bouton Secondaire")
                gr.Button("Bouton Principal", variant="primary")

    # On utilise gr.HTML pour injecter notre code JavaScript dans la page
    gr.HTML(f"<script>{js_code}</script>", visible=False)

    # 1. Au chargement de la page, exécute `on_load` pour régler le Radio sur la bonne couleur
    demo.load(
        fn=None,
        js="on_load",
        inputs=None,
        outputs=color_selector
    )

    # 2. Quand une couleur est sélectionnée, exécute `on_select`
    color_selector.select(
        fn=None,
        js="on_select",
        inputs=[color_selector],
        outputs=None
    )


# Lance l'application. Pour que cela fonctionne, vous devez la lancer depuis un fichier.
# Le thème de base peut être défini ici, mais il sera écrasé par le paramètre d'URL.
demo.launch(share=True)

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://cbbf07367303490db9.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


In [ ]:
dict_order = {2:"Speechmatics", 3:"AssemblyAI",
              1:"Scribe v1", 0:"Whisper Large v3 Turbo"}

list_model = ["Speechmatics", "AssemblyAI",
              "Scribe v1", "Whisper Large v3 Turbo"]
list_color = ["violet", "yellow", "indigo", "green"]

for i in range(len(list_model)):
    print(f"{i}: {dict_order[i]}")
    ind = list_model.index(dict_order[i])
    print(f"{list_model[ind]} - {list_color[ind]}")

0: Whisper Large v3 Turbo
Whisper Large v3 Turbo - green
1: Scribe v1
Scribe v1 - indigo
2: Speechmatics
Speechmatics - violet
3: AssemblyAI
AssemblyAI - yellow


In [ ]:
import gradio as gr

# Define the function that takes a name and returns a greeting.
def greet(name):
    return "Hello " + name + "!", name

# Create a Gradio interface with custom CSS to change the label color to red.
with gr.Blocks(css="gradio-label { color: red; }") as demo:
    name = gr.Textbox(label="Name")
    output = gr.Textbox(label="Output Box")
    greet_btn = gr.Button("Greet")
    greet_btn.click(fn=greet, inputs=name, outputs=[output, result])

demo.launch(show_error=True)

NameError: name 'result' is not defined

In [ ]:
!pip show datasets

Name: datasets
Version: 4.0.0
Summary: HuggingFace community-driven open-source library of datasets
Home-page: https://github.com/huggingface/datasets
Author: HuggingFace Inc.
Author-email: thomas@huggingface.co
License: Apache 2.0
Location: /usr/local/lib/python3.11/dist-packages
Requires: dill, filelock, fsspec, huggingface-hub, multiprocess, numpy, packaging, pandas, pyarrow, pyyaml, requests, tqdm, xxhash
Required-by: torchtune
